# AnyCoder Demo Notebook

This notebook illustrates how to:

1. **Instantiate** the unified `hf_client` with automatic provider routing.
2. **Call** a chat completion (Groq → OpenAI → Gemini fall‑back).
3. **Trigger** the FastAPI `/predict` endpoint served by *app.py*.
4. **Run** a quick sentiment‑analysis pipeline using your preferred provider.

In [ ]:
# 1. Setup inference client
from hf_client import get_inference_client

# Choose a model (will route to best provider according to prefix rules)
model_id = 'openai/gpt-4'   # try 'gemini/pro' or any HF model path
client = get_inference_client(model_id, provider='auto')

# Simple chat completion
resp = client.chat.completions.create(
    model=model_id,
    messages=[{'role': 'user', 'content': 'Write a Python function to reverse a string.'}]
)
print(resp.choices[0].message.content)

In [ ]:
# 2. Sentiment analysis via HF Inference Providers (OpenAI GPT‑4)
from transformers import pipeline

sentiment = pipeline(
    'sentiment-analysis', 
    model='openai/gpt-4',      # could be 'gemini/pro' etc.
    trust_remote_code=True
)
sentiment('I love building AI‑powered tools!')

In [ ]:
# 3. Call the FastAPI /predict endpoint exposed by app.py
import json, requests

payload = {
    'prompt': 'Generate a minimal HTML page.',
    'model_id': 'gemini/pro',
    'language': 'html',
    'web_search': False
}

r = requests.post('http://localhost:7860/predict', json=payload)
print('Status:', r.status_code)
print(json.loads(r.text)['code'][:400])

---
## Next steps

* Switch `model_id` to **`'gemini/pro'`**, **`'fireworks-ai/fireworks-v1'`**, or any HF model (e.g. `Qwen/Qwen3-32B`)—routing will adjust automatically.
* Explore **`plugins.py`** for Slack / GitHub integrations.
* Use **`auth.py`** helpers to pull private Google Drive docs into the pipeline.
* Extend `/predict` with temperature, max‑tokens, or stream support.